# Priming neural networks with the correct initializer.

In this quick experiment, we will be testing the effect of different weight/bias initializations on a very simple variational autoencoder (VAE). We will be using the MNIST dataset to prototype. The VAE will essentially have 3 layes:
- an input layer of shape (784) that would represent a flattened MNIST image (28,28).
- a single hidden layer where the input will be "encoded" down from 784 features to 32.
- an output layer that "decodes" the hidden latent representation back into a MNIST image.

In [2]:
import numpy as np
import tensorflow as tf
import plotly
from tensorflow.examples.tutorials.mnist import input_data
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)
from plotly import tools
print ("tensorflow {}".format(tf.__version__))
print ("plotly {}".format(plotly.__version__))

tensorflow 1.4.1
plotly 2.2.3


## import data

In [3]:
mnist = input_data.read_data_sets('MNIST_data', validation_size=0)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


## set various initializations

Here we pick 8 different tensorflow initializations to test.

In [4]:
initializers = [
# we start with the no brainer zeros and ones and constants
{"type":tf.zeros_initializer(), "name":"zeros"},
{"type":tf.ones_initializer(), "name":"ones"},
    
# random distributions
{"type":tf.random_normal_initializer(mean=0.0,stddev=1.0), "name":"random_normal"},
{"type":tf.random_uniform_initializer(minval=0,maxval=1.0), "name":"random_uniform"},
    
# glorot or Xavier initalizations
{"type":tf.glorot_normal_initializer(), "name":"glorot_normal"},
{"type":tf.glorot_uniform_initializer(), "name":"glorot_uniform"},
    
# others
{"type":tf.orthogonal_initializer(gain=1.0), "name":"orthogonal"},
{"type":tf.initializers.identity(gain=1.0), "name":"identity"}  
]

# add a loss list and value list to each entry in the list
for entry in initializers:
    entry["loss"] = [] 
    entry["value"] = [] 

## visualize initialization distributions

We will run generate square 2d tensors of shape 100*100 from each initalizer and plot their distribution, just to get an idea about how tensorflow samples them.

In [30]:
tensor_dim_0 = 100
tensor_dim_1 = 100

In [31]:
# set initializer value
for initializer in initializers:
    tf.reset_default_graph()
    with tf.Graph().as_default():
        # set seed
        tf.set_random_seed(42)
        # set dummy variable
        var = tf.Variable(initial_value=tf.get_variable(shape=[tensor_dim_0,tensor_dim_1],
                                                        name = initializer['name'],
                                                        initializer=initializer['type']))
        sess = tf.Session()
        init = tf.global_variables_initializer()
        sess.run(init)
        initializer['value'] = sess.run(var)

In [32]:
# plot distributions
# make figure
fig = tools.make_subplots(rows=4, cols=2, subplot_titles=[x['name'] for x in initializers])
for idx,initializer in enumerate(initializers):
    # make trace
    x = np.reshape(initializer['value'],tensor_dim_0*tensor_dim_1)
    trace = go.Histogram(x=x,histnorm='',opacity=0.6)
    fig.append_trace(trace, (idx//2) + 1, (idx%2) + 1 )

    
fig['layout'].update(height=1200, 
                     width=1000, 
                     showlegend=False, 
                     title='Tensorflow initializer distribution - 10k samples',
                    font=dict(size=12))
iplot(fig) 
plot(fig,
     show_link=False,
     image_height=1200, 
     image_width=1000, 
     image_filename="histograms", 
     image="svg")

This is the format of your plot grid:
[ (1,1) x1,y1 ]  [ (1,2) x2,y2 ]
[ (2,1) x3,y3 ]  [ (2,2) x4,y4 ]
[ (3,1) x5,y5 ]  [ (3,2) x6,y6 ]
[ (4,1) x7,y7 ]  [ (4,2) x8,y8 ]



'file:///home/ahmed/Dropbox/medium/yhat/00000_priming_neural_networks_with_an appropriate_initializer/temp-plot.html'

## sanity check for the glorot initializers

Here, we will be manually calculating the statistcs of the glorot intializers. We will then compare that to the standard deviation of the values tensorflow gave us above. For the glorot_normal, we will check the standard deviation. For the glorot_uniform, we will check the limits. All looks good!

In [34]:
# from tensorflow - https://www.tensorflow.org/api_docs/python/tf/glorot_normal_initializer
# stddev = sqrt(2 / (fan_in + fan_out))
stddev_calculated = np.sqrt(2 / (tensor_dim_0 + tensor_dim_1))
stddev_actual = np.std(np.reshape(initializers[4]['value'],100*100))
print ("glorot_normal_initializer std: " ,stddev_calculated, stddev_actual)

# from tensorflow - https://www.tensorflow.org/api_docs/python/tf/glorot_uniform_initializer
# limit = sqrt(6 / (fan_in + fan_out))
limit_calculated = np.sqrt(6 / (tensor_dim_0 + tensor_dim_1))
limit_actual = np.max(initializers[5]['value'])
print ("glorot_uniform_initializer limit: " ,limit_calculated, limit_actual)

glorot_normal_initializer std:  0.1 0.0886468
glorot_uniform_initializer limit:  0.173205080757 0.173109


## build model

In [7]:
epochs = 10
batch_size = 200

for initializer in initializers:
    tf.reset_default_graph()
    with tf.Graph().as_default():
        # set seed
        tf.set_random_seed(42)
        hidden_size = 32 
        # set weight and bias
        weight = {
            "i_h" : tf.Variable(initial_value=tf.get_variable(shape=[784,hidden_size],
                                                name="weight_i_h",
                                                initializer=initializer['type'])), 
            "h_o" : tf.Variable(initial_value=tf.get_variable(shape=[hidden_size,784],
                                                name="weight_h_o",
                                                initializer=initializer['type'])) 
        }  
        bias = {
            "i_h" : tf.Variable(initial_value= tf.zeros([hidden_size]) ),
            "h_o" :  tf.Variable(initial_value= tf.zeros([784]) ),
        }
        # placeholders
        _inputs = tf.placeholder(dtype=tf.float32,shape=[None,784],name="input_placeholder")
        _targets = tf.placeholder(dtype=tf.float32 ,shape=[None,784],name="target_placeholder")
        # encode
        encode = tf.nn.relu( tf.nn.bias_add ( tf.matmul(_inputs,weight["i_h"]) , bias["i_h"] ) ) 
        # logits
        logits =  tf.nn.bias_add( tf.matmul(encode,weight["h_o"]), bias["h_o"]) 
        # sigmoid 
        decode = tf.nn.sigmoid(logits)
        # cross-entropy 
        loss = tf.nn.sigmoid_cross_entropy_with_logits(logits=logits,labels=_targets)
        # mean
        cost = tf.reduce_mean(loss)
        # optimizer
        opt = tf.train.AdamOptimizer(learning_rate=0.001).minimize(cost)
        # session
        sess = tf.Session()
        init = tf.global_variables_initializer()
        sess.run(init)
        # run
        for epoch in range(epochs):
            for i in range(mnist.train.num_examples//batch_size):
                batch = mnist.train.next_batch(batch_size,shuffle=False)
                feed = {_inputs:batch[0],_targets:batch[0]}
                batch_cost, _ = sess.run([ cost, opt], feed_dict=feed)
                # add to list
                initializer['loss'].append(batch_cost)
                print("Epoch: {}/{} - ".format(epoch+1, epochs),"Training loss: {:.4f}".format(batch_cost))

Epoch: 1/10 -  Training loss: 0.6933
Epoch: 1/10 -  Training loss: 0.6930
Epoch: 1/10 -  Training loss: 0.6922
Epoch: 1/10 -  Training loss: 0.6919
Epoch: 1/10 -  Training loss: 0.6918
Epoch: 1/10 -  Training loss: 0.6914
Epoch: 1/10 -  Training loss: 0.6909
Epoch: 1/10 -  Training loss: 0.6904
Epoch: 1/10 -  Training loss: 0.6903
Epoch: 1/10 -  Training loss: 0.6900
Epoch: 1/10 -  Training loss: 0.6894
Epoch: 1/10 -  Training loss: 0.6890
Epoch: 1/10 -  Training loss: 0.6889
Epoch: 1/10 -  Training loss: 0.6886
Epoch: 1/10 -  Training loss: 0.6879
Epoch: 1/10 -  Training loss: 0.6875
Epoch: 1/10 -  Training loss: 0.6874
Epoch: 1/10 -  Training loss: 0.6870
Epoch: 1/10 -  Training loss: 0.6866
Epoch: 1/10 -  Training loss: 0.6860
Epoch: 1/10 -  Training loss: 0.6860
Epoch: 1/10 -  Training loss: 0.6857
Epoch: 1/10 -  Training loss: 0.6851
Epoch: 1/10 -  Training loss: 0.6850
Epoch: 1/10 -  Training loss: 0.6846
Epoch: 1/10 -  Training loss: 0.6844
Epoch: 1/10 -  Training loss: 0.6839
E

Epoch: 1/10 -  Training loss: 0.6128
Epoch: 1/10 -  Training loss: 0.6121
Epoch: 1/10 -  Training loss: 0.6126
Epoch: 1/10 -  Training loss: 0.6114
Epoch: 1/10 -  Training loss: 0.6100
Epoch: 1/10 -  Training loss: 0.6096
Epoch: 1/10 -  Training loss: 0.6100
Epoch: 1/10 -  Training loss: 0.6098
Epoch: 1/10 -  Training loss: 0.6097
Epoch: 1/10 -  Training loss: 0.6096
Epoch: 1/10 -  Training loss: 0.6095
Epoch: 1/10 -  Training loss: 0.6115
Epoch: 1/10 -  Training loss: 0.6099
Epoch: 1/10 -  Training loss: 0.6082
Epoch: 1/10 -  Training loss: 0.6072
Epoch: 1/10 -  Training loss: 0.6059
Epoch: 1/10 -  Training loss: 0.6048
Epoch: 1/10 -  Training loss: 0.6087
Epoch: 1/10 -  Training loss: 0.6053
Epoch: 1/10 -  Training loss: 0.6069
Epoch: 1/10 -  Training loss: 0.6071
Epoch: 1/10 -  Training loss: 0.6062
Epoch: 1/10 -  Training loss: 0.6047
Epoch: 1/10 -  Training loss: 0.6037
Epoch: 1/10 -  Training loss: 0.6053
Epoch: 1/10 -  Training loss: 0.6048
Epoch: 1/10 -  Training loss: 0.6031
E

Epoch: 2/10 -  Training loss: 0.5481
Epoch: 2/10 -  Training loss: 0.5473
Epoch: 2/10 -  Training loss: 0.5462
Epoch: 2/10 -  Training loss: 0.5499
Epoch: 2/10 -  Training loss: 0.5464
Epoch: 2/10 -  Training loss: 0.5487
Epoch: 2/10 -  Training loss: 0.5504
Epoch: 2/10 -  Training loss: 0.5474
Epoch: 2/10 -  Training loss: 0.5450
Epoch: 2/10 -  Training loss: 0.5448
Epoch: 2/10 -  Training loss: 0.5464
Epoch: 2/10 -  Training loss: 0.5442
Epoch: 2/10 -  Training loss: 0.5515
Epoch: 2/10 -  Training loss: 0.5436
Epoch: 2/10 -  Training loss: 0.5441
Epoch: 2/10 -  Training loss: 0.5442
Epoch: 2/10 -  Training loss: 0.5463
Epoch: 2/10 -  Training loss: 0.5451
Epoch: 2/10 -  Training loss: 0.5380
Epoch: 2/10 -  Training loss: 0.5449
Epoch: 2/10 -  Training loss: 0.5452
Epoch: 2/10 -  Training loss: 0.5455
Epoch: 2/10 -  Training loss: 0.5430
Epoch: 2/10 -  Training loss: 0.5482
Epoch: 2/10 -  Training loss: 0.5422
Epoch: 2/10 -  Training loss: 0.5394
Epoch: 2/10 -  Training loss: 0.5431
E

Epoch: 3/10 -  Training loss: 0.5030
Epoch: 3/10 -  Training loss: 0.5021
Epoch: 3/10 -  Training loss: 0.4970
Epoch: 3/10 -  Training loss: 0.5010
Epoch: 3/10 -  Training loss: 0.4939
Epoch: 3/10 -  Training loss: 0.5006
Epoch: 3/10 -  Training loss: 0.4965
Epoch: 3/10 -  Training loss: 0.4905
Epoch: 3/10 -  Training loss: 0.4870
Epoch: 3/10 -  Training loss: 0.4951
Epoch: 3/10 -  Training loss: 0.4945
Epoch: 3/10 -  Training loss: 0.4948
Epoch: 3/10 -  Training loss: 0.4857
Epoch: 3/10 -  Training loss: 0.4908
Epoch: 3/10 -  Training loss: 0.4920
Epoch: 3/10 -  Training loss: 0.4892
Epoch: 3/10 -  Training loss: 0.4893
Epoch: 3/10 -  Training loss: 0.4894
Epoch: 3/10 -  Training loss: 0.4912
Epoch: 3/10 -  Training loss: 0.4945
Epoch: 3/10 -  Training loss: 0.4955
Epoch: 3/10 -  Training loss: 0.4965
Epoch: 3/10 -  Training loss: 0.4906
Epoch: 3/10 -  Training loss: 0.4914
Epoch: 3/10 -  Training loss: 0.4955
Epoch: 3/10 -  Training loss: 0.4937
Epoch: 3/10 -  Training loss: 0.4875
E

Epoch: 4/10 -  Training loss: 0.4508
Epoch: 4/10 -  Training loss: 0.4532
Epoch: 4/10 -  Training loss: 0.4541
Epoch: 4/10 -  Training loss: 0.4518
Epoch: 4/10 -  Training loss: 0.4496
Epoch: 4/10 -  Training loss: 0.4649
Epoch: 4/10 -  Training loss: 0.4619
Epoch: 4/10 -  Training loss: 0.4613
Epoch: 4/10 -  Training loss: 0.4647
Epoch: 4/10 -  Training loss: 0.4598
Epoch: 4/10 -  Training loss: 0.4532
Epoch: 4/10 -  Training loss: 0.4539
Epoch: 4/10 -  Training loss: 0.4538
Epoch: 4/10 -  Training loss: 0.4559
Epoch: 4/10 -  Training loss: 0.4504
Epoch: 4/10 -  Training loss: 0.4571
Epoch: 4/10 -  Training loss: 0.4556
Epoch: 4/10 -  Training loss: 0.4494
Epoch: 4/10 -  Training loss: 0.4629
Epoch: 4/10 -  Training loss: 0.4586
Epoch: 4/10 -  Training loss: 0.4515
Epoch: 4/10 -  Training loss: 0.4516
Epoch: 4/10 -  Training loss: 0.4622
Epoch: 4/10 -  Training loss: 0.4588
Epoch: 4/10 -  Training loss: 0.4602
Epoch: 4/10 -  Training loss: 0.4549
Epoch: 4/10 -  Training loss: 0.4506
E

...

Epoch: 7/10 -  Training loss: 0.2260
Epoch: 7/10 -  Training loss: 0.2457
Epoch: 7/10 -  Training loss: 0.2406
Epoch: 7/10 -  Training loss: 0.2381
Epoch: 7/10 -  Training loss: 0.2337
Epoch: 7/10 -  Training loss: 0.2456
Epoch: 7/10 -  Training loss: 0.2426
Epoch: 7/10 -  Training loss: 0.2289
Epoch: 7/10 -  Training loss: 0.2223
Epoch: 7/10 -  Training loss: 0.2396
Epoch: 7/10 -  Training loss: 0.2538
Epoch: 7/10 -  Training loss: 0.2407
Epoch: 7/10 -  Training loss: 0.2262
Epoch: 7/10 -  Training loss: 0.2552
Epoch: 7/10 -  Training loss: 0.2271
Epoch: 7/10 -  Training loss: 0.2270
Epoch: 7/10 -  Training loss: 0.2210
Epoch: 7/10 -  Training loss: 0.2257
Epoch: 7/10 -  Training loss: 0.2316
Epoch: 7/10 -  Training loss: 0.2230
Epoch: 7/10 -  Training loss: 0.2259
Epoch: 7/10 -  Training loss: 0.2173
Epoch: 7/10 -  Training loss: 0.2216
Epoch: 7/10 -  Training loss: 0.2250
Epoch: 7/10 -  Training loss: 0.2294
Epoch: 7/10 -  Training loss: 0.2318
Epoch: 7/10 -  Training loss: 0.2405
E

Epoch: 8/10 -  Training loss: 0.2176
Epoch: 8/10 -  Training loss: 0.2269
Epoch: 8/10 -  Training loss: 0.2283
Epoch: 8/10 -  Training loss: 0.2319
Epoch: 8/10 -  Training loss: 0.2192
Epoch: 8/10 -  Training loss: 0.2313
Epoch: 8/10 -  Training loss: 0.2333
Epoch: 8/10 -  Training loss: 0.2169
Epoch: 8/10 -  Training loss: 0.2177
Epoch: 8/10 -  Training loss: 0.2187
Epoch: 8/10 -  Training loss: 0.2309
Epoch: 8/10 -  Training loss: 0.2295
Epoch: 8/10 -  Training loss: 0.2307
Epoch: 8/10 -  Training loss: 0.2259
Epoch: 8/10 -  Training loss: 0.2216
Epoch: 8/10 -  Training loss: 0.2086
Epoch: 8/10 -  Training loss: 0.2191
Epoch: 8/10 -  Training loss: 0.2423
Epoch: 8/10 -  Training loss: 0.2198
Epoch: 8/10 -  Training loss: 0.2204
Epoch: 8/10 -  Training loss: 0.2242
Epoch: 8/10 -  Training loss: 0.2266
Epoch: 8/10 -  Training loss: 0.2450
Epoch: 8/10 -  Training loss: 0.2353
Epoch: 8/10 -  Training loss: 0.2319
Epoch: 8/10 -  Training loss: 0.2343
Epoch: 8/10 -  Training loss: 0.2248
E

Epoch: 8/10 -  Training loss: 0.2347
Epoch: 8/10 -  Training loss: 0.2281
Epoch: 8/10 -  Training loss: 0.2166
Epoch: 8/10 -  Training loss: 0.2386
Epoch: 8/10 -  Training loss: 0.2256
Epoch: 8/10 -  Training loss: 0.2412
Epoch: 8/10 -  Training loss: 0.2272
Epoch: 8/10 -  Training loss: 0.2254
Epoch: 8/10 -  Training loss: 0.2129
Epoch: 8/10 -  Training loss: 0.2226
Epoch: 8/10 -  Training loss: 0.2253
Epoch: 8/10 -  Training loss: 0.2224
Epoch: 8/10 -  Training loss: 0.2113
Epoch: 8/10 -  Training loss: 0.2211
Epoch: 8/10 -  Training loss: 0.2360
Epoch: 8/10 -  Training loss: 0.2335
Epoch: 8/10 -  Training loss: 0.2289
Epoch: 8/10 -  Training loss: 0.2201
Epoch: 8/10 -  Training loss: 0.2279
Epoch: 8/10 -  Training loss: 0.2062
Epoch: 8/10 -  Training loss: 0.2219
Epoch: 8/10 -  Training loss: 0.2125
Epoch: 8/10 -  Training loss: 0.2203
Epoch: 8/10 -  Training loss: 0.2236
Epoch: 8/10 -  Training loss: 0.2247
Epoch: 8/10 -  Training loss: 0.2163
Epoch: 8/10 -  Training loss: 0.2193
E

Epoch: 9/10 -  Training loss: 0.2212
Epoch: 9/10 -  Training loss: 0.2362
Epoch: 9/10 -  Training loss: 0.2253
Epoch: 9/10 -  Training loss: 0.2241
Epoch: 9/10 -  Training loss: 0.2297
Epoch: 9/10 -  Training loss: 0.2335
Epoch: 9/10 -  Training loss: 0.2295
Epoch: 9/10 -  Training loss: 0.2299
Epoch: 9/10 -  Training loss: 0.2191
Epoch: 9/10 -  Training loss: 0.2206
Epoch: 9/10 -  Training loss: 0.2303
Epoch: 9/10 -  Training loss: 0.2277
Epoch: 9/10 -  Training loss: 0.2331
Epoch: 9/10 -  Training loss: 0.2252
Epoch: 9/10 -  Training loss: 0.2232
Epoch: 9/10 -  Training loss: 0.2251
Epoch: 9/10 -  Training loss: 0.2182
Epoch: 9/10 -  Training loss: 0.2341
Epoch: 9/10 -  Training loss: 0.2190
Epoch: 9/10 -  Training loss: 0.2159
Epoch: 9/10 -  Training loss: 0.2276
Epoch: 9/10 -  Training loss: 0.2186
Epoch: 9/10 -  Training loss: 0.2205
Epoch: 9/10 -  Training loss: 0.2245
Epoch: 9/10 -  Training loss: 0.2188
Epoch: 9/10 -  Training loss: 0.2239
Epoch: 9/10 -  Training loss: 0.2432
E

Epoch: 10/10 -  Training loss: 0.2360
Epoch: 10/10 -  Training loss: 0.2217
Epoch: 10/10 -  Training loss: 0.2273
Epoch: 10/10 -  Training loss: 0.2497
Epoch: 10/10 -  Training loss: 0.2426
Epoch: 10/10 -  Training loss: 0.2230
Epoch: 10/10 -  Training loss: 0.2198
Epoch: 10/10 -  Training loss: 0.2150
Epoch: 10/10 -  Training loss: 0.2274
Epoch: 10/10 -  Training loss: 0.2188
Epoch: 10/10 -  Training loss: 0.2318
Epoch: 10/10 -  Training loss: 0.2253
Epoch: 10/10 -  Training loss: 0.2158
Epoch: 10/10 -  Training loss: 0.2204
Epoch: 10/10 -  Training loss: 0.2459
Epoch: 10/10 -  Training loss: 0.2224
Epoch: 10/10 -  Training loss: 0.2302
Epoch: 10/10 -  Training loss: 0.2361
Epoch: 10/10 -  Training loss: 0.2333
Epoch: 10/10 -  Training loss: 0.2351
Epoch: 10/10 -  Training loss: 0.2221
Epoch: 10/10 -  Training loss: 0.2251
Epoch: 10/10 -  Training loss: 0.2295
Epoch: 10/10 -  Training loss: 0.2265
Epoch: 10/10 -  Training loss: 0.2024
Epoch: 10/10 -  Training loss: 0.2236
Epoch: 10/10

## plot batch loss

In [13]:
plot_data = []
for initializer in initializers:
    trace = go.Scatter(
        x = np.arange(len(initializer['loss'])),
        y = initializer['loss'],
        name = initializer['name']
    )
    plot_data.append(trace)

layout = go.Layout(
    title = "Step loss with different weight initialization",
    xaxis=dict(
        showgrid=True,
        title="steps",
        range=[0,500]
    ),
    yaxis=dict(
        showgrid=True,
        title="loss",
        range=[0,2]
    ),
    autosize=True,
    showlegend=True,
)

fig = go.Figure(data=plot_data, layout=layout)
iplot(fig  )

In [ ]:
for initializer in initializers:
    print (initializer['name'])
